# Glossary Making Tool

This is a Work-in-progress experiment tool to make living glossaries Webpages using simple Python, Javascript, and CSS from an markdown file written in a Etherpad instance.

**What makes it living?** 

* The glossary structure uses the idea of 'gloss' that means annottation and layer. It makes the glossary a layering of anotations rather than a list of definitions. The pad template uses each word as a card with multiple annotations. See the example.

* This tool also offers the option of add properties to each word in order to find connections and multiple types of organization. 


## Words
Communicating via **API** with the glossary **Pad** and translating the text written in **Markdown** format using **Pandoc** library.

In [11]:
import json, pypandoc
from urllib.request import urlopen
from urllib.parse import urlencode


with open("/opt/etherpad/APIKEY.txt") as f:
    api_key = f.read().strip()

api_url = "https://hub.xpub.nl/soupboat/pad/api/1.2.15/"

# wrap in a convenient function (APICALL)
def ep (api_fn, api_url, api_key, **data):
    data['apikey'] = api_key
    return json.load(urlopen(f"{api_url}{api_fn}", data=urlencode(data).encode()))


glossary = ep("getText", api_url, api_key, padID="binding_glossary")

text = glossary["data"]["text"]

words = pypandoc.convert_text(text, 'html', format='md')

From a local markdown text file

In [12]:
import pypandoc

text = open('glossary.txt', 'r')

with text as f:
    text = f.read()
    
words = pypandoc.convert_text(text, 'html', format='md')

## Properties

The following is a word property dictionary 

In [13]:
properties = [
	{
		'title':'fact',
		'symbol':'A',
        'color': 'green'
	},
	{
		'title':'process',
		'symbol':'S',
		'color': 'aqua'
	},
	{
		'title':'love',
		'symbol':'L',
		'color': 'orange'
	},
    	{
		'title':'tool',
		'symbol':'T',
		'color': 'blue'
	}
]

## Writing the Website

Write properties legend

In [14]:
description = ''

i = 0

for title, symbol, color in properties:
    title = properties[i]['title']
    description += (f''' {title}s,''')
    i += 1

In [15]:
legend = ''

i = 0

for title, symbol, color in properties:
    title = properties[i]['title']
    legend += f'''<button id="{title}" class="btn {title}-s" onclick="filterSelection('{title}')">{title}</button>\n'''
    i += 1

Write Script that will add properties to each word

In [16]:
script = ''

i = 0 

for title, symbol, color in properties:
    title = properties[i]['title']
    symbol = properties[i]['symbol']
    script += (f"""const {title} = document.getElementsByClassName("{title}");
    for (let i = 0; i < {title}.length; i++)"""'{\n' 
               f"""{title}[i].innerHTML += "<span class='symbol {title}-s'>{symbol}</span>";""" 
    '\n}\n\n')
    i += 1

Assign a different color for each property 

In [17]:
style = ''

i = 0 

for title, symbol, color in properties:
    title = properties[i]['title']
    color = properties[i]['color']
    style += f'''.{title}-s''' + '{' + f'''color:{color};''''}'
    i += 1

In [18]:
body = f'''<!DOCTYPE html>
    <html>
    <head>
        <meta charset="utf-8">
        <meta name="viewport" content="width=device-width, initial-scale=1">
        <link rel="stylesheet" href="style.css"> 
        <title>Binding GLossary</title>
    </head>
        <style> {style} </style>
    <body id="glo_body">

    <div class="head">
        <h1> Glossary for a Diffractive Publishing Practice </h1>
    </div>
    <hr>
    <div class="description">
        <p>This glossary gathers words around bookbiding. It was made as an example to use the tool living-glossary.</p> 
        <p>{description} are the properties that organize and make connections between words.</p>
    </div>
    <div id="legend" class="legend"> 
        <button class="btn active" onclick="filterSelection('all')">properties</button> {legend}
    </div>
    <hr>
    <div class="words">
        {words} 
    </div>
    </body>
        <script>
            {script}
        </script>
        <script src="main.js"></script>
    </html>'''

website = open('index.html','w')

website.write(body)
website.close()

In [ ]:
print(words)

In [ ]:
from time import sleep

while True:
    print('hey')
    sleep(5)